In [3]:
import numpy as np
import pandas as pd
import plotly.express as px
from math import *

In [168]:
main_surface_label = "main surface"
gradient_point_label = "gradient point"
x_label = "x"
y_label = "y"
z_label = "z"
color_label = "color"


def plot_2d_graph(df, description):
    fig = px.scatter(df, x=x_label, y=y_label, color=color_label)
    fig.update_layout(title_text=description)
    fig.show()


def plot_3d_graph(df, description):
    fig = px.scatter_3d(df, x=x_label, y=y_label, z=z_label, color=color_label, color_continuous_scale=z_label)
    fig.update_layout(title_text=description)
    fig.show()


def plot_heat_3d_graph(df, description):
    fig = px.scatter_3d(df, x=x_label, y=y_label, z=z_label, color=z_label)
    fig.update_layout(title_text=description)
    fig.show()


def get_splitted_data_arrays(data):
    x_data = []
    y_data = []
    z_data = []
    for value in data:
        x_data.append(value[0])
        y_data.append(value[1])
        z_data.append(value[2])
    return x_data, y_data, z_data

In [182]:
from scipy import optimize

from typing import Callable


def find_gradient_at_point_3d(func: Callable, point):
    eps = np.sqrt(np.finfo(float).eps)
    return optimize.approx_fprime(point, func, [eps, np.sqrt(200) * eps])


def find_gradient_at_point_2d(func: Callable, point):
    return optimize.approx_fprime(point, func)


def draw_gradient_descent_3d(z_lambda, data, start_point, max_step_counter=10000, epsilon_strategy=1):
    delta = pow(10, -6)
    if epsilon_strategy == 1:
        epsilon = pow(10, -3)
    else:
        epsilon = 1
    current_gradient_value = start_point
    current_x, current_y = current_gradient_value
    current_z = z_lambda([current_x, current_y])
    previous_gradient_value = None
    data.append((current_x, current_y, current_z, gradient_point_label))
    step_counter = 0
    while (previous_gradient_value is None or np.linalg.norm(
            current_gradient_value - previous_gradient_value) > delta) and step_counter < max_step_counter:
        previous_gradient_value = current_gradient_value
        current_gradient_value = current_gradient_value - epsilon * find_gradient_at_point_3d(z_lambda,
                                                                                              current_gradient_value)
        current_x, current_y = current_gradient_value
        current_z = z_lambda((current_x, current_y))
        data.append((current_x, current_y, current_z, gradient_point_label))
        step_counter += 1
        if epsilon_strategy == 2:
            epsilon = epsilon / 2
    df = pd.DataFrame(data, columns=[x_label, y_label, z_label, color_label])
    plot_3d_graph(df, f"Min of function found in {current_gradient_value}. Steps count = {step_counter}")


def draw_gradient_descent_2d(y_lambda, data, start_point, max_step_counter=10000, epsilon_strategy=1):
    delta = pow(10, -4)
    if epsilon_strategy == 1:
        epsilon = pow(10, -1)
    else:
        epsilon = 1
    current_gradient_value = start_point
    current_x = current_gradient_value[0]
    current_y = y_lambda([current_x])
    previous_gradient_value = None
    data.append((current_x, current_y, gradient_point_label))
    step_counter = 0
    while (previous_gradient_value is None or np.linalg.norm(
            current_gradient_value - previous_gradient_value) > delta) and step_counter < max_step_counter:
        previous_gradient_value = current_gradient_value
        current_gradient_value = current_gradient_value - epsilon * find_gradient_at_point_2d(y_lambda,
                                                                                              current_gradient_value)
        current_x = current_gradient_value[0]
        current_y = y_lambda([current_x])
        data.append((current_x, current_y, gradient_point_label))
        step_counter += 1
        if epsilon_strategy == 2:
            epsilon = epsilon / 2
    df = pd.DataFrame(data, columns=[x_label, y_label, color_label])
    plot_2d_graph(df, f"Min of function found in {current_gradient_value}. Steps count = {step_counter}")

In [186]:
from_value = -1
to_value = 1

from_x = from_value
to_x = to_value
steps = 100
h = (to_value - from_value) / steps
y_lambda = lambda x: x[0] ** 2
data = []
for i in range(steps + 1):
    x = from_x + i * h
    y = y_lambda([x])
    data.append((x, y, main_surface_label))
# plot_2d_graph(pd.DataFrame(data, columns=[x_label, y_label, color_label]), "Main surface")
draw_gradient_descent_2d(y_lambda, data, [0.75], epsilon_strategy=2)

In [187]:
draw_gradient_descent_2d(y_lambda, data, [0.75], epsilon_strategy=1)

In [184]:
from_value = -2 * pi
to_value = 2 * pi

from_x = from_value
to_x = to_value
steps = 100
h = (to_value - from_value) / steps
y_lambda = lambda x: sin(x[0])
data = []
for i in range(steps + 1):
    x = from_x + i * h
    y = y_lambda([x])
    data.append((x, y, main_surface_label))
draw_gradient_descent_2d(y_lambda, data, [0.75], epsilon_strategy=2)

In [185]:
draw_gradient_descent_2d(y_lambda, data, [0.75], epsilon_strategy=1)

In [170]:
from_value = -1
to_value = 1

from_x = from_value
to_x = to_value
from_y = from_value
to_y = to_value
steps = 100
h = (to_value - from_value) / steps
z_lambda = lambda x: x[0] ** 2 + x[1] ** 2
data = []
for i in range(steps + 1):
    x = from_x + i * h
    for j in range(steps + 1):
        y = from_y + j * h
        z = z_lambda((x, y))
        data.append((x, y, z, main_surface_label))
# plot_3d_graph(pd.DataFrame(data, columns=[x_label, y_label, z_label, color_label]), "Main surface")
draw_gradient_descent_3d(z_lambda, data, (1, 1))

In [171]:
from_value = -1
to_value = 1

from_x = from_value
to_x = to_value
from_y = from_value
to_y = to_value
steps = 100
h = (to_value - from_value) / steps
z_lambda = lambda x: sin(x[0]) + x[1] ** 2
data = []
for i in range(steps + 1):
    x = from_x + i * h
    for j in range(steps + 1):
        y = from_y + j * h
        z = z_lambda((x, y))
        data.append((x, y, z, main_surface_label))
# plot_3d_graph(pd.DataFrame(data, columns=[x_label, y_label, z_label, color_label]), "Main surface")
draw_gradient_descent_3d(z_lambda, data, (1, 1))

In [175]:
from_value = -(pi / 2)
to_value = pi / 2

from_x = from_value
to_x = to_value
from_y = from_value
to_y = to_value
steps = 100
h = (to_value - from_value) / steps
z_lambda = lambda x: cos(x[0]) + abs(x[1] ** 3 + 3 * x[1] ** 2 + 17 * x[1])
data = []
for i in range(steps + 1):
    x = from_x + i * h
    for j in range(steps + 1):
        y = from_y + j * h
        z = z_lambda((x, y))
        data.append((x, y, z, main_surface_label))
# plot_3d_graph(pd.DataFrame(data, columns=[x_label, y_label, z_label, color_label]), "Main surface")
draw_gradient_descent_3d(z_lambda, data, (0, 1))

In [146]:
from_value = -1
to_value = 1

from_x = from_value
to_x = to_value
from_y = from_value
to_y = to_value
steps = 10
h = (to_value - from_value) / steps
z_lambda = lambda x: x[0] + x[1] ** 3
data = []
for i in range(steps + 1):
    x = from_x + i * h
    for j in range(steps + 1):
        y = from_y + j * h
        z = z_lambda((x, y))
        data.append((x, y, z, main_surface_label))
plot_3d_graph(pd.DataFrame(data, columns=[x_label, y_label, z_label, color_label]), "Main surface")
draw_gradient_descent_3d(z_lambda, data, (0.5, 0.5))